# Detector de objetos Yolov8x  para la especie 2(Nine-banded Armadillo)

In [ ]:
import cv2
import torch
from ultralytics import YOLO
import os
import pandas as pd
import hashlib
import numpy as np

# Definir las rutas de entrada y salida
input_xlsx = '/home/emontenegrob/dataset_frames_conf/top_6_species_split_dataset.xlsx'  # Archivo Excel de entrada
output_folder = '/home/emontenegrob/frames_pilot_3_3/'  # Carpeta principal para guardar los frames
dataset_xlsx = '/home/emontenegrob/dataset_frames_conf/dataset_frames_3_3.xlsx'  # Nombre del archivo Excel de salida

# Verificar si CUDA está disponible
device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(f"Dispositivo en uso: {device}")

# Leer el archivo Excel para obtener los videos relevantes
df_input = pd.read_excel(input_xlsx)

# Filtrar por el ID de la especie 
species_id_paca = 3  # ID de la especie correspondiente

# Filtrar por el ID de la especie y partición (train, test, validation)
filtered_videos = df_input[(df_input['species_id'] == species_id_paca) &
                           (df_input['splitdata_pilot'].isin(['train', 'test', 'validation']))]

# Si no hay videos que cumplan con los criterios, salir del script
if filtered_videos.empty:
    print("No se encontraron videos para la especie especificada.")
    exit()

# Crear las carpetas de salida para los splits (train, test, validation)
folders = {
    'train': os.path.join(output_folder, 'frames_train'),
    'test': os.path.join(output_folder, 'frames_test'),
    'validation': os.path.join(output_folder, 'frames_val')
}

# Crear las carpetas si no existen
for folder in folders.values():
    if not os.path.exists(folder):
        os.makedirs(folder)

# Cargar el modelo YOLOv8 preentrenado
model = YOLO('yolov8x.pt').to(device)  # Modelo ligero; puedes cambiarlo por uno más grande si es necesario

# Lista para almacenar la información del dataset final
data = []

# Función para enmascarar el logo naranja basado en su color
def enmascarar_logo_naranja(frame):
    # Convertir la imagen de BGR a HSV
    hsv = cv2.cvtColor(frame, cv2.COLOR_BGR2HSV)
    
    # Definir el rango de colores para el color naranja del logo
    lower_orange = np.array([5, 100, 100])  # Valores aproximados para el naranja
    upper_orange = np.array([15, 255, 255]) # Valores aproximados para el naranja

    # Crear una máscara que detecte los píxeles en el rango de naranja
    mask = cv2.inRange(hsv, lower_orange, upper_orange)

    # Enmascarar el área detectada (convertirla a negro)
    frame[mask > 0] = (0, 0, 0)

    return frame

# Procesar **todos** los videos filtrados
for index, video in filtered_videos.iterrows():
    video_path = video['path_video_linux']
    split = video['splitdata_pilot']  # Obtener el tipo de split (train, test, validation)

    # Determinar la carpeta de salida según el split
    output_split_folder = folders.get(split)

    if not output_split_folder:
        print(f"Error: No se encontró carpeta para el split '{split}'")
        continue

    # Procesar cada video
    print(f"Procesando el video: {video_path} para el split: {split}")

    # Verificar si el video existe
    if not os.path.exists(video_path):
        print(f"El video no existe: {video_path}")
        continue

    # Leer el video con manejo de excepciones
    try:
        cap = cv2.VideoCapture(video_path)
        if not cap.isOpened():
            raise Exception(f"No se puede abrir el video: {video_path}")
    except Exception as e:
        print(e)
        cap.release()
        continue

    # Obtener el SHA256 del video
    sha256_video = hashlib.sha256(open(video_path, 'rb').read()).hexdigest()

    # Configurar para analizar solo la mitad del video
    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))  # Total de frames en el video
    max_frames_to_analyze = total_frames // 2  # Solo la mitad del video

    frame_count = 0
    confidence_threshold = 0.55  # Umbral de confianza ajustado a 0.55

    while True:
        ret, frame = cap.read()

        if not ret or frame_count >= max_frames_to_analyze:  # Termina si no hay más frames o si se alcanzó el límite de 450 frames
            break

        # Enmascarar el logo naranja antes de realizar la detección
        frame = enmascarar_logo_naranja(frame)

        # Realizar la detección de objetos en los frames
        results = model(frame)

        # Obtener las predicciones directamente de los resultados
        detections = results[0].boxes

        # Filtrar solo detecciones con suficiente confianza
        animal_detected = False
        bbox_coords = None  # Inicializar la variable de coordenadas del bounding box
        for det in detections:
            class_id = int(det.cls[0])
            confidence = det.conf[0].item()  # Convertir tensor a valor numérico
            if confidence >= confidence_threshold:  # Solo guardar los frames con confianza >= 0.55
                # Dibuja el bounding box en el frame
                x1, y1, x2, y2 = map(int, det.xyxy[0])  # Coordenadas del bounding box
                cv2.rectangle(frame, (x1, y1), (x2, y2), (0, 255, 0), 1)  # Dibujar el cuadro
                cv2.putText(frame, f'Conf: {confidence:.2f}', (x1, y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)
                animal_detected = True

                # Guardar las coordenadas del bounding box en formato (x1, y1, x2, y2)
                bbox_coords = f"({x1}, {y1}, {x2}, {y2})"

        # Guardar el frame si se detectó un animal
        if animal_detected:
            frame_filename = os.path.join(output_split_folder, f"{os.path.basename(video_path).split('.')[0]}_frame_{frame_count:04d}.png")
            cv2.imwrite(frame_filename, frame)

            # Calcular el sha256 de la imagen guardada
            with open(frame_filename, "rb") as f:
                bytes = f.read()
                sha256_image = hashlib.sha256(bytes).hexdigest()

            # Añadir la información al dataset
            data.append({
                "Path del Video": video_path,
                "Frame (imagen luego del algoritmo de detección de movimiento)": frame_filename,
                "ID": video['species_id'],  # Usar el ID de la especie
                "Especie": video['species_name'],
                "Tipo": video['tipo'],
                "sha256 (del video)": sha256_video,
                "sha256 de la imagen": sha256_image,
                "Partition": video['splitdata_pilot'],  # Utilizar la partición existente
                "Bounding Box": bbox_coords,  # Guardar las coordenadas del bounding box
                "Confianza": confidence  # Guardar el valor de confianza de la detección
            })
            print(f"Frame guardado con bounding box para {video_path}: {frame_filename}, Confianza: {confidence:.2f}")

        frame_count += 1

    cap.release()

# Crear un DataFrame con la información recopilada
df_output = pd.DataFrame(data)

# Guardar el DataFrame en un archivo Excel
df_output.to_excel(dataset_xlsx, index=False, engine='openpyxl')

print(f"Proceso completado. Se han analizado y guardado frames con confianza >= {confidence_threshold} de la mitad de los videos.")


Dispositivo en uso: cuda


100%|██████████| 131M/131M [00:02<00:00, 50.8MB/s] 


Procesando el video: /home/emontenegrob/nov-dic-21/PAJARO TORO (0mtrs)/100EK113/12080070.AVI para el split: validation

0: 384x640 (no detections), 132.2ms
Speed: 5.0ms preprocess, 132.2ms inference, 18.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 16.0ms
Speed: 1.4ms preprocess, 16.0ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 16.0ms
Speed: 1.5ms preprocess, 16.0ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 16.0ms
Speed: 1.4ms preprocess, 16.0ms inference, 0.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 16.0ms
Speed: 1.4ms preprocess, 16.0ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 16.0ms
Speed: 1.4ms preprocess, 16.0ms inference, 0.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 14.3ms
Speed: 1.4ms preprocess, 14.3ms inference, 0